In [2]:
import geopandas as gpd
import fiona
import osmnx as ox
import folium
import pandas as pd 
from fiona.model import to_dict
from shapely.geometry import shape
from branca.colormap import LinearColormap
import numpy as np
import networkx as nx
import matplotlib.pyplot as plt
from scipy.spatial import Voronoi,voronoi_plot_2d
from geovoronoi import voronoi_regions_from_coords, points_to_coords
import random
from shapely.geometry import Polygon, Point
from skmob.tessellation.tilers import tiler
from skmob.utils.plot import plot_gdf

In [3]:
# piste ciclabili di Leuven 

cycling = gpd.read_file('https://storageaccount11111111.blob.core.windows.net/container1/Leuven/cycling_data/cycling_network.gpkg', crs={'init':'epsg:31370'})
cycling = cycling.to_crs(epsg=4326)

In [179]:
# hubs 
hubs = gpd.read_file('https://storageaccount11111111.blob.core.windows.net/container1/Leuven/hub_data_leuven/mobility_hubs.gpkg', crs={'init':'epsg:31370'})
hubs = hubs.to_crs(epsg=4326)
column_name_translations = {
    'X': 'Longitude',
    'Y': 'Latitude',
    'nr': 'Number',
    'naam punt': 'Point Name',
    'Deelgemeente': 'Sub-municipality',
    'openbaar vervoer': 'Public Transport',
    'AWV': 'Roads and Traffic Agency',
    'OD of andere': 'Other',
    'Herkoms': 'Origin',
    'Interregionaal': 'Interregional',
    'Tijdstip lancering eHUB': 'eHUB Launch Time',
    'realistische timing': 'Realistic Timing',
    'publieke fietsenstalling': 'Public Bike Storage',
    'publieke parking': 'Public Parking',
    'Pakjesautomaat': 'Parcel Machine',
    'Blue Bike': 'Blue Bike',
    'aantal deelwagens': 'Number of Shared Cars',
    'aantal laadpalen': 'Number of Charging Stations',
    'aantal e-deelwagens': 'Number of Electric Shared Cars',
    'type zuil': 'Pillar Type',
    'aantal deelwagens (Uitbr 2020)': 'Number of Shared Cars (Expansion in 2020)',
    'aantal e-deelwagens (uitbr 2020)': 'Number of Electric Shared Cars (Expansion in 2020)',
    'aantal laadpalen (dossier 2020 - voorzien voor Q1 2021)': 'Number of Charging Stations (File 2020 - Planned for Q1 2021)',
    'aantal deelwagens (scenario2)': 'Number of Shared Cars (Scenario 2)',
    'aantal e-deelwagens (scenario2)': 'Number of Electric Shared Cars (Scenario 2)',
    'e-deelfietsen Sept (30)': 'E-bikes in September (30)',
    'e-deelfietsen Maart (35)': 'E-bikes in March (35)',
    'e-deelfietsen Mei (40)': 'E-bikes in May (40)',
    'e-deelfietsen Toekomst? (60)': 'E-bikes in the Future? (60)',
    'aantal deelfietsen': 'Number of Shared Bikes',
    'aantal e-deelfietsen (indien max 92 0)': 'Number of Electric Shared Bikes (if max 92 0)',
    'aantal e-deelfietsen (indien max 125)': 'Number of Electric Shared Bikes (if max 125)',
    'aantal e-deelfietsen (indien max 125) scenario 26 locaties': 'Number of Electric Shared Bikes (if max 125) scenario 26 locations',
    'aantal e-deelfietsen (indien max 125) scenario 31 locaties': 'Number of Electric Shared Bikes (if max 125) scenario 31 locations',
    'aantal e-deelbakfietsen': 'Number of Electric Cargo Bikes',
    'aantal pakjesautomaten': 'Number of Parcel Machines',
    '# fietsbeugels te voorzien': 'Number of Bike Racks to be Provided',
    'aantal e-hubs': 'Number of E-hubs',
    'EV capaciteit': 'Electric Vehicle Capacity',
    'stadsgezicht': 'Cityscape',
    'geometry': 'geometry'
}

hubs = hubs.rename(columns=column_name_translations)

In [9]:
point = (50.849738563227824, 4.644786576420597)
m = folium.Map(location = point, zoom_start = 12)
for index, hub in hubs.iterrows():
    lon, lat = hub['Longitude'], hub['Latitude']

    feature1 = hub['Point Name']
    feature2 = f"Number of Shared Cars: {hub['Number']}"
    feature3 = f"Public Transport: {hub['Public Transport']}"
    feature4 = f"Number of Shared Bikes: {hub['Number of Shared Bikes']}"
    feature5 = f"Number of Electric Shared Cars: {hub['Number of Electric Shared Cars']}"
    feature6 = f"Number of Charging Stations: {hub['Number of Charging Stations']}"

    popup_text = f"<strong>{feature1}</strong><br>{feature2}<br>{feature3}<br>{feature4}<br>{feature5}<br>{feature6}"


    marker = folium.Marker(
        location=[lat, lon],
        popup=popup_text,
        icon=folium.Icon(color='blue')
    )


    marker.add_to(m)

folium.GeoJson(cycling).add_to(m)


In [10]:

def style(fill_color, border_color, spessore_contorno=2, opacita=0.5):
    return {
        'fillColor': fill_color,
        'color': border_color,
        'weight': spessore_contorno,
        'fillOpacity': opacita
    }

### IDEA CON TESSELLATION

In [11]:
point = (50.849738563227824, 4.644786576420597)
m = folium.Map(location=point, zoom_start = 12)

pappalord's random voronoi tessellation

In [12]:
tess_squared = tiler.get('squared', base_shape='Leuven, Belgium', meters=1000)
print("tiles = %s" %len(tess_squared))
print(tess_squared['geometry'][0].centroid)

tiles = 192
POINT (4.644786576420597 50.849738563227824)


In [14]:

def get_convex_hull(tess):
    polygon = tess.at[0, 'geometry']
    for tile in tess['geometry']:
        polygon = polygon.union(tile)
    return polygon.convex_hull

poly_ch = get_convex_hull(tess_squared)
# print(poly_ch)

POLYGON ((4.65826130568239 50.82420960000001, 4.640295 50.84690277800979, 4.640295 50.88092185764183, 4.667244458523585 50.94322571319334, 4.6852107642059755 50.94888556480272, 4.712160222729562 50.94888556480272, 4.739109681253147 50.94322571319334, 4.748092834094342 50.93756517246947, 4.766059139776733 50.909252131130565, 4.775042292617928 50.89225603512331, 4.775042292617928 50.87525373477279, 4.748092834094342 50.841230517975404, 4.694193917047171 50.82420960000001, 4.65826130568239 50.82420960000001))


In [52]:
for index, hub in hubs.iterrows():
    lon, lat = hub['Longitude'], hub['Latitude']

    feature1 = hub['Point Name']
    feature2 = f"Number of Shared Cars: {hub['Number']}"
    feature3 = f"Public Transport: {hub['Public Transport']}"
    feature4 = f"Number of Shared Bikes: {hub['Number of Shared Bikes']}"
    feature5 = f"Number of Electric Shared Cars: {hub['Number of Electric Shared Cars']}"
    feature6 = f"Number of Charging Stations: {hub['Number of Charging Stations']}"

    popup_text = f"<strong>{feature1}</strong><br>{feature2}<br>{feature3}<br>{feature4}<br>{feature5}<br>{feature6}"


    marker = folium.Marker(
        location=[lat, lon],
        popup=popup_text,
        icon=folium.Icon(color='blue')
    )


    marker.add_to(m)

folium.GeoJson(cycling).add_to(m)
#folium.GeoJson(tess_voronoi).add_to(m)
m

### ISOCHRONE

In [43]:
place = 'Leuven, Belgium'
network_type = 'bike'
threshold = 15
travel_speed = 8.5 #walking speed in km/hour

In [44]:
G = ox.graph_from_place(place, network_type=network_type)

In [45]:
# find the centermost node and then project the graph to UTM
gdf_nodes = ox.graph_to_gdfs(G, edges=False)
x, y = gdf_nodes['geometry'].unary_union.centroid.xy
x,y

(array('d', [4.705631245277631]), array('d', [50.87869028892212]))

In [46]:
center_node = ox.nearest_nodes(G, Y = y[0], X = x[0])
G = ox.project_graph(G)

In [47]:
# add an edge attribute for time in minutes required to traverse each edge
meters_per_minute = travel_speed * 1000 / 60 #km per hour to m per minute
for u, v, k, data in G.edges(data=True, keys=True):
    data['time'] = data['length'] / meters_per_minute

In [26]:
# get one color for each isochrone
iso_colors = ox.plot.get_colors(n=1, cmap='plasma', start=0, return_hex=True)
iso_colors

['#0d0887']

In [77]:
G.nodes[center_node]

{'y': 5637704.517425226,
 'x': 619984.5875639291,
 'street_count': 3,
 'lon': 4.7055251,
 'lat': 50.8785461}

In [ ]:
# color the nodes according to isochrone then plot the street network
node_colors = {}

subgraph = nx.ego_graph(G, center_node, radius=threshold, distance='time')
for node in subgraph.nodes():
    node_colors[node] = '#0d0887'
nc = [node_colors[node] if node in node_colors else 'none' for node in G.nodes()]
ns = [15 if node in node_colors else 0 for node in G.nodes()]
fig, ax = ox.plot_graph(G, node_color=nc, node_size=ns, node_alpha=0.8, node_zorder=2,
                        bgcolor='k', edge_linewidth=0.2, edge_color='#999999')



In [ ]:
for e in subgraph.nodes():
    w = nx.shortest_path_length(subgraph, center_node, e, weight= 'time')
    if 10 <= w <= 15:
        print(center_node, e, w)
        print(G.nodes[e])

# OD MATRIX

In [15]:
od = gpd.read_file('https://storageaccount11111111.blob.core.windows.net/container1/Leuven/od_data_leuven/OD_zones_leuven.gpkg')
od = od.to_crs('EPSG:4326')
od_leuven = od[od['VREGIO_L'] == 'LEUVEN']
point = ((cycling['geometry'][41]).coords[0][1], (cycling['geometry'][41]).coords[0][0])
m = folium.Map(location=point, zoom_start = 12)
folium.GeoJson(od_leuven).add_to(m)
m

In [16]:
folium.GeoJson(poly_ch, style_function=lambda x: style('red', 'red')).add_to(m)

In [19]:
od = od_leuven[od_leuven['geometry'].intersects(poly_ch) == True]

In [10]:
point = ((cycling['geometry'][41]).coords[0][1], (cycling['geometry'][41]).coords[0][0])
m = folium.Map(location=point, zoom_start = 12)
folium.GeoJson(od).add_to(m)
m

In [137]:
matrice = pd.read_excel(r"C:\Users\Valeria\Downloads\OD_Matrix_Leuven_2017.xlsx", sheet_name='PW_08', index_col=0) # macchine ore 8 


In [138]:
for reg in od['ZONENUMMER']:
    if reg not in list(matrice.columns):
        od.drop(od.loc[od['ZONENUMMER'] == reg].index, inplace=True)

In [132]:
od

ZONENUMMER  STGB        STGB_L  NIS_GEM           NIS_GEM_L  VREGIO  \
1584        1585     1  STUDIEGEBIED    24009        24009 BERTEM       7   
1585        1586     1  STUDIEGEBIED    24009        24009 BERTEM       7   
1586        1587     1  STUDIEGEBIED    24009        24009 BERTEM       7   
1587        1588     1  STUDIEGEBIED    24009        24009 BERTEM       7   
1599        1600     1  STUDIEGEBIED    24011      24011 BIERBEEK       7   
...          ...   ...           ...      ...                 ...     ...   
2006        2007     1  STUDIEGEBIED    24086  24086 OUD-HEVERLEE       7   
2007        2008     1  STUDIEGEBIED    24086  24086 OUD-HEVERLEE       7   
2008        2009     1  STUDIEGEBIED    24086  24086 OUD-HEVERLEE       7   
2009        2010     1  STUDIEGEBIED    24086  24086 OUD-HEVERLEE       7   
2010        2011     1  STUDIEGEBIED    24086  24086 OUD-HEVERLEE       7   

     VREGIO_L                                           geometry  
1584   LEUVEN  MULTIPOLYGON (((4.63580 50.86224, 4.63544 50.8...  
1585   LEUVEN  MULTIPOLYGON (((4.62842 50.84880, 4.62771 50.8...  
1586   LEUVEN  MULTIPOLYGON (((4.60700 50.85648, 4.60684 50.8...  
1587   LEUVEN  MULTIPOLYGON (((4.62200 50.82821, 4.62179 50.8...  
1599   LEUVEN  MULTIPOLYGON (((4.75764 50.82984, 4.75722 50.8...  
...       ...                                                ...  
2006   LEUVEN  MULTIPOLYGON (((4.71189 50.82604, 4.71119 50.8...  
2007   LEUVEN  MULTIPOLYGON (((4.71335 50.81114, 4.71282 50.8...  
2008   LEUVEN  MULTIPOLYGON (((4.72667 50.82892, 4.72626 50.8...  
2009   LEUVEN  MULTIPOLYGON (((4.72295 50.82344, 4.72257 50.8...  
2010   LEUVEN  MULTIPOLYGON (((4.72318 50.82274, 4.72298 50.8...  

[179 rows x 8 columns]

In [133]:
matrice

1212       1584       1585      1586     1587     1588     1589     \
1212       0.948   0.000000   0.000000  0.000000    0.920    0.952    0.000   
1584       0.000  10.060000   6.064000  1.078000    0.715    0.933    2.836   
1585       0.000   7.338000  15.502000  0.860000    2.702    2.599    0.892   
1586       0.000   0.449000   0.504000  0.000000    0.000    0.000    0.000   
1587       0.000   1.386000   2.710000  0.000000    1.739    0.000    0.000   
...          ...        ...        ...       ...      ...      ...      ...   
1000033    0.000   0.000000   0.000000  0.000000    0.000    0.000    0.000   
1000034    0.000   2.294743  12.433414  2.404907    0.000    0.000    4.144   
1000035    0.000   0.000000   0.000000  0.000000    0.000    0.000    0.000   
1000036    0.000   0.270000   0.000000  0.000000    0.000    0.000    0.000   
1000037    0.046   3.840000   2.876000  0.000000    1.095    0.334    1.852   

         1590     1591     1592     ...      1000028  1000029    1000030  \
1212       0.000    0.000    0.000  ...     0.000000    5.295   0.000000   
1584       0.000    2.689    0.000  ...    53.075974    0.000  12.328000   
1585       0.877    3.912    0.000  ...   126.821158    0.000  15.316000   
1586       0.000    0.000    0.000  ...     9.406000    0.000   0.597000   
1587       0.000    0.819    0.786  ...    21.499000    0.000   5.133000   
...          ...      ...      ...  ...          ...      ...        ...   
1000033    0.000    0.000    0.000  ...     7.736000    0.000   0.000000   
1000034    3.527   18.963    1.038  ...     0.000000    0.000   0.000000   
1000035    0.000    0.000    0.000  ...     0.000000    0.000   0.000000   
1000036    0.000    0.000    0.000  ...     0.000000    0.000   0.000000   
1000037    0.410    3.133    0.059  ...  1678.705183    0.000  45.521733   

         1000031  1000032  1000033  1000034  1000035  1000036  1000037  
1212       0.963    0.000      0.0    0.000      0.0      0.0        0  
1584       0.000    0.977      0.0    6.704      0.0      0.0        0  
1585       0.000    0.000      0.0   23.782      0.0      0.0        0  
1586       0.000    0.000      0.0    3.869      0.0      0.0        0  
1587       0.000    0.000      0.0    1.102      0.0      0.0        0  
...          ...      ...      ...      ...      ...      ...      ...  
1000033    0.000    0.000      0.0    0.000      0.0      0.0        0  
1000034    0.000    0.000      0.0    0.000      0.0      0.0        0  
1000035    0.000    0.000      0.0    0.000      0.0      0.0        0  
1000036    0.000    0.000      0.0    0.000      0.0      0.0        0  
1000037    0.000    0.000      0.0    0.496      0.0      0.0        0  

[286 rows x 286 columns]

In [139]:
matrice = matrice[list(od['ZONENUMMER'])]
matrice = matrice.filter(items = list(od['ZONENUMMER']), axis=0)
matrice

1585  1586   1587   1588   1600   1601   1603   1604   1605   1606  \
1585  15.502  0.86  2.702  2.599  0.000  0.000  0.000  0.000  0.000  0.000   
1586   0.504  0.00  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
1587   2.710  0.00  1.739  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
1588   0.803  0.00  0.000  1.950  0.000  0.000  0.000  0.478  0.000  0.000   
1600   0.000  0.00  0.000  0.000  0.770  0.903  0.000  0.000  0.000  0.000   
...      ...   ...    ...    ...    ...    ...    ...    ...    ...    ...   
2007   0.000  0.00  0.000  0.000  0.000  0.000  0.000  0.885  0.000  0.000   
2008   0.000  0.00  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
2009   0.115  0.00  0.000  0.000  0.000  0.000  2.244  0.000  0.000  0.929   
2010   0.000  0.00  0.000  0.000  0.858  0.000  1.916  0.000  1.846  1.949   
2011   0.000  0.00  0.000  0.000  0.000  0.000  0.000  0.965  2.780  0.916   

      ...   2001   2002   2003  2004   2005   2007   2008   2009   2010   2011  
1585  ...  0.000  0.967  1.667   0.0  0.000  0.000  0.000  0.000  0.000  0.000  
1586  ...  0.000  0.000  0.000   0.0  0.000  0.000  0.000  0.000  0.000  0.000  
1587  ...  0.000  0.000  0.000   0.0  0.000  0.000  0.000  0.000  0.000  0.000  
1588  ...  0.000  0.000  0.956   0.0  0.000  0.000  0.000  0.000  0.701  0.000  
1600  ...  0.000  0.000  0.000   0.0  0.160  0.000  0.000  0.000  0.938  0.903  
...   ...    ...    ...    ...   ...    ...    ...    ...    ...    ...    ...  
2007  ...  0.000  0.000  0.000   0.0  1.475  2.919  0.000  0.000  1.748  0.965  
2008  ...  0.000  0.000  0.000   0.0  0.863  0.000  0.000  0.000  0.718  1.852  
2009  ...  0.847  0.000  0.000   0.0  2.478  1.517  0.000  1.294  6.637  4.509  
2010  ...  0.000  0.000  1.843   0.0  3.709  0.904  0.920  7.531  3.086  3.792  
2011  ...  0.000  0.000  0.967   0.0  4.169  0.000  1.852  3.188  3.709  3.048  

[179 rows x 179 columns]

In [140]:
G = nx.MultiDiGraph()

for source in matrice.index:
    for target, weight in matrice.loc[source].items():
        G.add_edge(source, target, weight=weight)

print(G.edges(data=True))

[(1585, 1585, {'weight': 15.502}), (1585, 1586, {'weight': 0.86}), (1585, 1587, {'weight': 2.702}), (1585, 1588, {'weight': 2.599}), (1585, 1600, {'weight': 0.0}), (1585, 1601, {'weight': 0.0}), (1585, 1603, {'weight': 0.0}), (1585, 1604, {'weight': 0.0}), (1585, 1605, {'weight': 0.0}), (1585, 1606, {'weight': 0.0}), (1585, 1607, {'weight': 0.0}), (1585, 1608, {'weight': 1.138}), (1585, 1705, {'weight': 0.0}), (1585, 1708, {'weight': 0.0}), (1585, 1709, {'weight': 0.0}), (1585, 1715, {'weight': 0.0}), (1585, 1716, {'weight': 0.0}), (1585, 1717, {'weight': 0.857}), (1585, 1718, {'weight': 0.0}), (1585, 1719, {'weight': 0.0}), (1585, 1720, {'weight': 0.0}), (1585, 1721, {'weight': 0.0}), (1585, 1722, {'weight': 0.0}), (1585, 1723, {'weight': 0.0}), (1585, 1724, {'weight': 0.0}), (1585, 1725, {'weight': 0.731}), (1585, 1726, {'weight': 1.723}), (1585, 1727, {'weight': 0.0}), (1585, 1728, {'weight': 0.0}), (1585, 1729, {'weight': 0.0}), (1585, 1730, {'weight': 0.0}), (1585, 1731, {'weight'

In [143]:
regioni = {}
for id in list(matrice.columns): 
    indice = (od.loc[od['ZONENUMMER'] == id].index).tolist()[0]
    # lon, lat = round(od['geometry'][indice].centroid.x, 5), round(od['geometry'][indice].centroid.y, 5)
    regioni[id] = od['geometry'][indice]

In [144]:
regioni

{1585: <MULTIPOLYGON (((4.636 50.862, 4.635 50.863, 4.635 50.863, 4.635 50.863, 4.6...>,
 1586: <MULTIPOLYGON (((4.628 50.849, 4.628 50.849, 4.627 50.849, 4.627 50.85, 4.62...>,
 1587: <MULTIPOLYGON (((4.607 50.856, 4.607 50.856, 4.606 50.857, 4.606 50.857, 4.6...>,
 1588: <MULTIPOLYGON (((4.622 50.828, 4.622 50.828, 4.621 50.829, 4.621 50.828, 4.6...>,
 1600: <MULTIPOLYGON (((4.758 50.83, 4.757 50.83, 4.757 50.83, 4.757 50.831, 4.756 ...>,
 1601: <MULTIPOLYGON (((4.742 50.843, 4.741 50.843, 4.741 50.844, 4.741 50.844, 4.7...>,
 1603: <MULTIPOLYGON (((4.767 50.858, 4.766 50.858, 4.764 50.859, 4.763 50.859, 4.7...>,
 1604: <MULTIPOLYGON (((4.755 50.858, 4.755 50.858, 4.754 50.859, 4.754 50.859, 4.7...>,
 1605: <MULTIPOLYGON (((4.759 50.848, 4.759 50.848, 4.759 50.848, 4.758 50.848, 4.7...>,
 1606: <MULTIPOLYGON (((4.77 50.861, 4.768 50.861, 4.768 50.861, 4.768 50.861, 4.76...>,
 1607: <MULTIPOLYGON (((4.743 50.858, 4.743 50.858, 4.742 50.858, 4.741 50.858, 4.7...>,
 1608: <MULTIPOLYGON 

In [145]:
G = nx.MultiDiGraph()

for id, geo in regioni.items():
    G.add_node(id, pos=geo)


In [146]:
for source in matrice.index:
    for target, weight in matrice.loc[source].items():
        G.add_edge(source, target, weight=weight)

In [147]:
len(G.nodes(data=True))

179

In [148]:
edges = G.edges(data=True)
edge_data = [(u, v, data['weight']) for u, v, data in edges]
df_edges = pd.DataFrame(edge_data, columns=['source', 'target', 'weight'])

In [149]:
df_edges

source  target  weight
0        1585    1585  15.502
1        1585    1586   0.860
2        1585    1587   2.702
3        1585    1588   2.599
4        1585    1600   0.000
...       ...     ...     ...
32036    2011    2007   0.000
32037    2011    2008   1.852
32038    2011    2009   3.188
32039    2011    2010   3.709
32040    2011    2011   3.048

[32041 rows x 3 columns]

In [150]:
gdf_nodes = gpd.GeoDataFrame(G.nodes(data=True), columns=['AreaID', 'pos'])
gdf_nodes

AreaID                                                pos
0      1585  {'pos': MULTIPOLYGON (((4.635801259110914 50.8...
1      1586  {'pos': MULTIPOLYGON (((4.6284189623676575 50....
2      1587  {'pos': MULTIPOLYGON (((4.606998448711061 50.8...
3      1588  {'pos': MULTIPOLYGON (((4.621997846634538 50.8...
4      1600  {'pos': MULTIPOLYGON (((4.757636624791733 50.8...
..      ...                                                ...
174    2007  {'pos': MULTIPOLYGON (((4.711885172226054 50.8...
175    2008  {'pos': MULTIPOLYGON (((4.713354731792145 50.8...
176    2009  {'pos': MULTIPOLYGON (((4.726670779706881 50.8...
177    2010  {'pos': MULTIPOLYGON (((4.722946045680409 50.8...
178    2011  {'pos': MULTIPOLYGON (((4.723180438495515 50.8...

[179 rows x 2 columns]

In [151]:
geom = []
for diz in gdf_nodes['pos']:
    geom.append(diz['pos'])

In [152]:
tess = gpd.GeoDataFrame(data=gdf_nodes['AreaID'])
tess['geom'] = geom
tess = pd.merge(tess, df_edges.groupby('source').sum()['weight'], left_on = 'AreaID', right_on = 'source')
tess.rename(columns={'AreaID':'tile_ID', 'weight':'outflow', 'geom':'geometry'}, inplace=True)
tess

tile_ID                                           geometry  outflow
0       1585  MULTIPOLYGON (((4.635801259110914 50.862240710...  115.143
1       1586  MULTIPOLYGON (((4.6284189623676575 50.84879951...   18.596
2       1587  MULTIPOLYGON (((4.606998448711061 50.856480817...   26.828
3       1588  MULTIPOLYGON (((4.621997846634538 50.828214816...   58.071
4       1600  MULTIPOLYGON (((4.757636624791733 50.829841613...   26.226
..       ...                                                ...      ...
174     2007  MULTIPOLYGON (((4.711885172226054 50.826044550...   31.169
175     2008  MULTIPOLYGON (((4.713354731792145 50.811137106...   10.118
176     2009  MULTIPOLYGON (((4.726670779706881 50.828922930...   46.440
177     2010  MULTIPOLYGON (((4.722946045680409 50.823441207...   79.544
178     2011  MULTIPOLYGON (((4.723180438495515 50.822741697...   66.548

[179 rows x 3 columns]

In [103]:
import skmob

In [153]:
tess = gpd.GeoDataFrame(tess)
#tess['geometry']=tess['geometry'].apply(lambda x: Point(x))
tess.set_geometry(col=tess['geometry'])

tile_ID                                           geometry  outflow
0       1585  MULTIPOLYGON (((4.63580 50.86224, 4.63544 50.8...  115.143
1       1586  MULTIPOLYGON (((4.62842 50.84880, 4.62771 50.8...   18.596
2       1587  MULTIPOLYGON (((4.60700 50.85648, 4.60684 50.8...   26.828
3       1588  MULTIPOLYGON (((4.62200 50.82821, 4.62179 50.8...   58.071
4       1600  MULTIPOLYGON (((4.75764 50.82984, 4.75722 50.8...   26.226
..       ...                                                ...      ...
174     2007  MULTIPOLYGON (((4.71189 50.82604, 4.71119 50.8...   31.169
175     2008  MULTIPOLYGON (((4.71335 50.81114, 4.71282 50.8...   10.118
176     2009  MULTIPOLYGON (((4.72667 50.82892, 4.72626 50.8...   46.440
177     2010  MULTIPOLYGON (((4.72295 50.82344, 4.72257 50.8...   79.544
178     2011  MULTIPOLYGON (((4.72318 50.82274, 4.72298 50.8...   66.548

[179 rows x 3 columns]

In [154]:
df_edges

source  target  weight
0        1585    1585  15.502
1        1585    1586   0.860
2        1585    1587   2.702
3        1585    1588   2.599
4        1585    1600   0.000
...       ...     ...     ...
32036    2011    2007   0.000
32037    2011    2008   1.852
32038    2011    2009   3.188
32039    2011    2010   3.709
32040    2011    2011   3.048

[32041 rows x 3 columns]

In [155]:
fdf = skmob.FlowDataFrame(df_edges, origin='source', destination='target', flow='weight', tessellation=tess)

c:\Users\Valeria\anaconda3\envs\skmob\lib\site-packages\skmob\core\flowdataframe.py:145: UserWarning: The tessellation crs is None. It will be set to the default crs WGS84 (EPSG:4326).
  warn("The tessellation crs is None. It will be set to the default crs WGS84 (EPSG:4326).")


In [156]:
fdf

origin destination    flow
0       1585        1585  15.502
1       1585        1586   0.860
2       1585        1587   2.702
3       1585        1588   2.599
4       1585        1600   0.000
...      ...         ...     ...
32036   2011        2007   0.000
32037   2011        2008   1.852
32038   2011        2009   3.188
32039   2011        2010   3.709
32040   2011        2011   3.048

[32041 rows x 3 columns]

In [214]:
n = folium.Map(location=point, zoom_start=12)
#hubs = gpd.read_file('https://storageaccount11111111.blob.core.windows.net/container1/Leuven/hub_data_leuven/mobility_hubs.gpkg', crs={'init':'epsg:31370'})
#hubs = hubs.to_crs(epsg=4326)

for index, hub in hubs.iterrows():
    lon, lat = hub['Longitude'], hub['Latitude']

    feature1 = hub['Point Name']
    feature2 = f"Number of Shared Cars: {hub['Number']}"
    feature3 = f"Public Transport: {hub['Public Transport']}"
    feature4 = f"Number of Shared Bikes: {hub['Number of Shared Bikes']}"
    feature5 = f"Number of Electric Shared Cars: {hub['Number of Electric Shared Cars']}"
    feature6 = f"Number of Charging Stations: {hub['Number of Charging Stations']}"

    popup_text = f"<strong>{feature1}</strong><br>{feature2}<br>{feature3}<br>{feature4}<br>{feature5}<br>{feature6}"


    marker = folium.Marker(
        location=[lat, lon],
        popup=popup_text,
        icon=folium.Icon(color='blue', fill_opacity=0.1)
    )


    marker.add_to(n)

# non penso che dalla funzione fdf.plot_flows si possa mettere un raggio dei nodi di origini adattivo rispetto all'outflow
# quindi questa sotto è una scorciatoia brutta per 'modificare' la dimensione dei nodi 

for idx, row in tess.iterrows():
    outflow = row['outflow']
    geometry = row['geometry']
    centroid = geometry.centroid.coords[0][::-1]  

    radius = outflow * 0.05

    folium.CircleMarker(
        location=centroid,
        radius=radius,
        color='red',
        fill=True,
        fill_color='red',
        fill_opacity=1,
        popup=f'Outflow: {outflow}'
    ).add_to(n)

#folium.GeoJson(cycling).add_to(n)

folium.GeoJson(od,style_function=lambda x: style('blue', 'blue', spessore_contorno=0.5, opacita=0.1)).add_to(n)
m = fdf.plot_flows(n, min_flow = 20, flow_color='red', flow_weight = 2, color_origin_point = 'red', flow_popup=True)
m

In [219]:
# uguale a prima ma senza i markers degli hubs 

h = folium.Map(location=point, zoom_start=12)

for idx, row in tess.iterrows():   
    outflow = row['outflow']
    geometry = row['geometry']
    centroid = geometry.centroid.coords[0][::-1]  

    radius = outflow * 0.1

    folium.CircleMarker(
        location=centroid,
        radius=radius,
        color='red',
        fill=True,
        fill_color='red',
        fill_opacity=1,
        popup=f'Outflow: {outflow}'
    ).add_to(h)

#folium.GeoJson(cycling).add_to(n)

folium.GeoJson(od,style_function=lambda x: style('blue', 'blue', spessore_contorno=0.5, opacita=0.1)).add_to(h)
g = fdf.plot_flows(h, min_flow = 20, flow_color='red', flow_weight = 1.5, color_origin_point = 'red', flow_popup=True)
g